In [3]:
import pandas as pd
import numpy as np
import os
import pickle

print(os.path.abspath('.'))

C:\Users\Chung Chi\PycharmProjects\datamining2


# Import dataset and final shaping

In [5]:
# Import datasets
X_full = pickle.load(open('./data/clean/X_flat.pkl', 'rb'))
Y_full = pickle.load(open('./data/clean/Y_flat.pkl', 'rb'))

print(X_full.shape)
print(Y_full.shape)
print(X_full.columns)
print(Y_full.columns)

(1577352, 108)
(1577352, 3)
Index(['key', 'pid_x', 'size_x', 'color', 'brand', 'rrp', 'mainCategory',
       'category', 'subCategory', 'releaseDate',
       ...
       'cat_7', 'cat_10', 'cat_16', 'cat_18', 'cat_24', 'cat_30', 'cat_33',
       'cat_36', 'cat_37', 'marketing_activity'],
      dtype='object', length=108)
Index(['key', 'date', 'sales'], dtype='object')


In [7]:
# Drop non-numeric columns; networks only take numeric input
keys_dates = pd.DataFrame(X_full['key']).join(X_full['date']) # Store for future lookups
drop_x_cols = ['key', 'pid_x', 'size_x', 'color', 'brand', 'rrp', 'date', 'day_of_week', 
               'mainCategory', 'category', 'subCategory', 'releaseDate', 
               'rrp', 'price']
drop_y_cols = ['key', 'date']
X = X_full.drop(drop_x_cols, axis=1)
Y = Y_full.drop(drop_y_cols, axis=1)

In [8]:
# Convert to numpy to reshape for input
X = X.as_matrix() # Each row has shape (num_vars,)
Y = Y.as_matrix() # Each row has shape (1,)

In [10]:
print(X.shape)

(1577352, 95)


# Model definition

In [12]:
# We need a data generator to create mini-batches of X, Y for us
# For training, X = [0:30], [1:31], ..., [62:92] (total 63 slices per product)
# For training, Y = [29], [30], ..., [91]
# For testing, X = [63:93], [64:94], ..., [93:123] (total 31 slices per product)
# For testing, Y = [92], [93], ..., [122]
# Check whether slices are correct!
class BatchGenerator(object):
    def __init__(self, num_samples, X, Y, batch_size, window_size, num_vars, start_day, end_day):
        self.num_samples = num_samples
        self.X = X
        self.Y = Y
        self.window_size = window_size
        self.batch_size = batch_size
        self.num_vars = num_vars
        self.start_day = start_day # 0 = day 1 (2017-10-01)
        self.end_day = end_day
        self.current_product = 0 # To keep track of which product we are at (of 12,824)
        self.current_day = 0 # To track which day of a product we are in (of 123)

    def generate(self):
        x = np.zeros((self.batch_size, self.window_size, self.num_vars))
        y = np.zeros((self.batch_size, 1)) # Should this be 3d?
        while True:
            for i in range(self.batch_size):
                if (self.current_day+self.start_day+self.window_size) > self.end_day:
                    # Go to next product, first day
                    self.current_product += 1
                    self.current_day = 0
                if self.current_product == self.num_samples:
                    # Go back to first product for next epoch
                    self.current_product = 0
                x[i,:,:] = self.X[self.current_product*123+self.current_day+self.start_day:
                                  self.current_product*123+self.current_day+self.start_day+
                                  self.window_size] # Max = [62:92]
                y[i,:] = self.Y[self.current_product*123+self.current_day+self.start_day+
                                self.window_size-1] # Max = [91]
                self.current_day += 1 
            yield x, y


In [14]:
NUM_SAMPLES = 12824 # Use this to reduce sample size for faster prototyping
WINDOW_SIZE = 30
num_vars = X.shape[1]
train_batch_size = 63 # To make 1 product = 1 batch
test_batch_size = 31 # To make 1 product = 1 batch

In [16]:
train_start_day = 0
train_end_day = 92 # 2017-10-01 to 2017-12-31
# test_start_day = 92 - WINDOW_SIZE + 1 # So the first window frame ends with 2018-01-01 prediction
# test_end_day = 123 # 2018-01-01 to 2018-01-31

train_data_generator = BatchGenerator(NUM_SAMPLES, X, Y, train_batch_size, WINDOW_SIZE, 
                                      num_vars, train_start_day, train_end_day)
# test_data_generator = BatchGenerator(NUM_SAMPLES, X, Y, test_batch_size, WINDOW_SIZE, 
#                                      num_vars, test_start_day, test_end_day)

# Model training

In [124]:
# Custom metric to get mean absolute difference
# Metric function is similar to a loss function
# except that the results from evaluating a metric are not used when training the model
import keras.backend as backend
def mean_abs_diff(y_true, y_pred):
    return backend.mean(backend.abs(y_true - y_pred))

In [184]:
# Using 5-layered MLP (idea from presentation by Matthias' team)
# Windowing model
# Model predicts only sales unit of last day of a window frame
# Model definition
from keras.models import Sequential
from keras.layers import Dense, Activation, TimeDistributed, LSTM, Flatten
from keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau

num_epochs = 50 # This is too low; can increase if we push training to the cloud
num_hidden = 64
# Monitor 'loss' instead of 'val_loss', because there is no way to validate actually
callbacks_list = [EarlyStopping(monitor='loss', patience=10), 
                  ModelCheckpoint(filepath='mlp_v1_best.h5', monitor='loss',save_best_only=True)]
# ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=2, verbose=1, mode='min', cooldown=0, min_lr=0)

model = Sequential()
model.add(Dense(num_hidden, input_shape=(WINDOW_SIZE, num_vars), activation='relu'))
model.add(Dense(num_hidden, activation='relu'))
model.add(Dense(num_hidden, activation='relu'))
model.add(Dense(num_hidden, activation='relu')) # Add dropout?
model.add(Flatten())
model.add(Dense(1, activation='relu')) # Need kernel_initializer?
model.compile(loss='mean_absolute_error', optimizer='adadelta') # To penalise big deviations more
print(model.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_56 (Dense)             (None, 30, 64)            6144      
_________________________________________________________________
dense_57 (Dense)             (None, 30, 64)            4160      
_________________________________________________________________
dense_58 (Dense)             (None, 30, 64)            4160      
_________________________________________________________________
dense_59 (Dense)             (None, 30, 64)            4160      
_________________________________________________________________
flatten_12 (Flatten)         (None, 1920)              0         
_________________________________________________________________
dense_60 (Dense)             (None, 1)                 1921      
Total params: 20,545
Trainable params: 20,545
Non-trainable params: 0
_________________________________________________________________
None


In [186]:
# Train LSTM; running this will take a while!
history = model.fit_generator(generator=train_data_generator.generate(),
                              steps_per_epoch=NUM_SAMPLES*(train_end_day-WINDOW_SIZE+1)/train_batch_size,
                              # validation_data=test_data_generator.generate(),
                              # validation_steps=NUM_SAMPLES*(test_end_day-test_start_day-WINDOW_SIZE+1)/test_batch_size, 
                              callbacks=callbacks_list,
                              epochs = num_epochs, verbose=1,
                              shuffle=False)

Epoch 1/50
    1/12824 [..............................] - ETA: 4:04 - loss: 0.0000e+00

    7/12824 [..............................] - ETA: 2:14 - loss: 0.0136    

   13/12824 [..............................] - ETA: 2:08 - loss: 0.0330

   19/12824 [..............................] - ETA: 2:05 - loss: 0.0535

   25/12824 [..............................] - ETA: 2:02 - loss: 0.0692

...

12804/12824 [============================>.] - ETA: 0s - loss: 0.2125

12810/12824 [============================>.] - ETA: 0s - loss: 0.2125

12816/12824 [============================>.] - ETA: 0s - loss: 0.2124

12822/12824 [============================>.] - ETA: 0s - loss: 0.2123

12824/12824 [==============================] - 119s 9ms/step - loss: 0.2123


In [176]:
# Save model and history for future reuse
model.save('mlp_mse_noval.h5')
with open('mlp_history_mse_noval', 'wb') as file_pi:
    pickle.dump(history.history, file_pi)

# Predict sample

In [178]:
from keras.models import load_model
model = load_model('mlp_v1_best.h5')

In [180]:
sample_product = 3022
sample_x = np.zeros(shape=(1, WINDOW_SIZE, num_vars))
sample_y = np.zeros(shape=(1, 1))

sample_x[0, :, :] = X[sample_product*123+63:sample_product*123+93]
print(sample_x[0, 29, :])

[ 18.    20.    27.    37.    35.    11.     5.     6.     4.     6.
   6.    13.    29.    28.    34.     5.     6.     9.     8.    11.
  23.    26.     7.    39.    40.    35.    27.    20.     0.     0.
   0.     1.     0.     0.     0.     0.     0.    92.   -19.28   0.
   0.     0.     0.     0.     0.     0.     0.     0.     0.     0.
   0.     0.     1.     0.     0.     0.     0.     0.     0.     0.
   0.     0.     0.     0.     0.     0.     0.     0.     0.     0.
   0.     0.     0.     0.     0.     0.     0.     0.     0.     0.
   1.     1.     0.     0.     0.     1.     0.     0.     0.     0.
   0.     0.     0.     0.     0.  ]


In [182]:
round(model.predict(sample_x)[0][0])

0.0

In [56]:
# Actual y value
print(Y[sample_product*123+92])

[18.]


In [137]:
# For future predictions, we have to replace the actual past sales with the predicted sales 
index = 3022 # Product index
predictions = []
product_data = np.zeros(shape=(1, 123, num_vars)) # A copy of the data for replacement
product_data[0, :, :] = X[index*123:index*123+123]

product_X = np.zeros(shape=(1, WINDOW_SIZE, num_vars)) # This will be pushed into model
for i in range(31):
    product_X[0, :, :] = product_data[0, 63+i:63+WINDOW_SIZE+i]
    predictions.insert(0, round(model.predict(product_X)[0][0]))
    # Update product data with predictions (we are not supposed to know the actual values)
    if i == 0:
        product_data[0, 93+i, 0] = predictions[0] # [93] = 2018-01-02 input
    elif i < 28:
        product_data[0, 93+i, 0:i+1] = predictions[0:i+1]
    elif i < 30: # No need to update for i = 30 (last prediction day)
        product_data[0, 93+i, 0:28] = predictions[0:28] # We keep taking the last 28 predictions
print(predictions)
predictions = predictions[::-1] # We have to reverse the list to get back original order
print(predictions)

[28.0, 25.0, 21.0, 20.0, 22.0, 26.0, 28.0, 30.0, 34.0, 36.0, 36.0, 34.0, 29.0, 23.0, 23.0, 20.0, 21.0, 22.0, 27.0, 31.0, 31.0, 35.0, 29.0, 27.0, 23.0, 10.0, 12.0, 7.0, 16.0, 16.0, 13.0]
[13.0, 16.0, 16.0, 7.0, 12.0, 10.0, 23.0, 27.0, 29.0, 35.0, 31.0, 31.0, 27.0, 22.0, 21.0, 20.0, 23.0, 23.0, 29.0, 34.0, 36.0, 36.0, 34.0, 30.0, 28.0, 26.0, 22.0, 20.0, 21.0, 25.0, 28.0]


# Predict all

In [116]:
# Helper functions
def pred_soldout_day(pred_sales, stock):
    """
    Helper function to predict soldout day
    """
    result = 15 if stock <= 3 else len(pred_sales) # If stock is too few, middle is a good guess
    for day in range(len(pred_sales)):
        stock -= pred_sales[day]
        if stock <= 0:
            return day+1
    return result

def load_test_set(set_number):
    """
    Helper function to load and prepare test set
    """
    test = pd.read_csv('./data/test/test_{}.csv'.format(str(set_number)), index_col=0, 
                       dtype={'pid': np.int32})
    test['key'] = test['pid'].astype(str) + test['size']
    
    def extract_soldout_day(row):
        soldout_day = row['sold_out_date'][-2:]
        return int(soldout_day[1]) if soldout_day[0] == 0 else int(soldout_day)
    
    test['soldout_day'] = test.apply(extract_soldout_day, axis=1)
    test['pred_soldout_day'] = np.nan
    return test

In [171]:
# Make predictions for all products and store them
test = load_test_set(0)
all_predictions = pd.DataFrame()

# We only make predictions for the products in the test set
for row in range(test.shape[0]):
    key = str(test.iloc[row]['key'])
    
    # Make predictions for current product
    index = int(keys_dates[keys_dates['key'] == key].index[0]/123) # Get starting row of product
    predictions = []
    product_data = np.zeros(shape=(1, 123, num_vars)) # A copy of the data for replacement
    product_data[0, :, :] = X[index*123:index*123+123]
    
    product_X = np.zeros(shape=(1, WINDOW_SIZE, num_vars)) # This will be pushed into model
    for i in range(31):
        product_X[0, :, :] = product_data[0, 63+i:63+WINDOW_SIZE+i]
        predictions.insert(0, round(model.predict(product_X)[0][0]))
        # Update product data with predictions (we are not supposed to know the actual values)
        if i == 0:
            product_data[0, 93+i, 0] = predictions[0] # [93] = 2018-01-02 input
        elif i < 28:
            product_data[0, 93+i, 0:i+1] = predictions[0:i+1]
        elif i < 30: # No need to update for i = 30 (last prediction day)
            product_data[0, 93+i, 0:28] = predictions[0:28] # Take only last 28 predictions
    predictions = predictions[::-1] # Reverse the list to get back original order
    all_predictions[key] = predictions

all_predictions.to_csv('./data/test/pred_mlp_baseline.csv', index=False)
print("Predictions complete")

Predictions complete


# Evaluate on test data

In [201]:
# Example
prod_pred = all_predictions['12985L'].as_matrix()
print(prod_pred)
print(pred_soldout_day(prod_pred, 50))

[13. 16. 16.  7. 12. 10. 23. 27. 29. 35. 31. 31. 27. 22. 21. 20. 23. 23.
 29. 34. 36. 36. 34. 30. 28. 26. 22. 20. 21. 25. 28.]
4


In [202]:
# Go through all test sets
for set_num in range(5):
    test = load_test_set(set_num)
    for row in range(test.shape[0]):
        key = test['key'][row]
        stock = test['stock'][row]
        key_pred = all_predictions[key].as_matrix()
        test['pred_soldout_day'][row] = pred_soldout_day(key_pred, stock)
    test.to_csv('./data/test/test_{}_result.csv'.format(str(set_num))) # Dump test set result
    print('Test {}: {}'.format(str(set_num), 
                               str(np.sqrt(sum(abs(test['pred_soldout_day'] - test['soldout_day']))))))

C:\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Test 0: 264.46360808247323


Test 1: 263.72902760219625
